In [ ]:
%matplotlib inline

# **Set Environment**

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive', force_remount=True)

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/gdrive


In [ ]:
#Change Location
import os
os.chdir("/content/gdrive/My Drive")

In [ ]:
!pwd

/content/gdrive/My Drive


In [ ]:
!ls

 blanket1-without-rotations.zip   Dataset5_FullDS_runResults.xlsx
 canvas1-without-rotations.zip	  DataSet6
 ceiling1-without-rotations.zip   glcm_features.pckl
'Colab Notebooks'		  glcm_features_us_ds5_folder0.pckl
 DataSet5			  Kylberg_Texture_Dataset


# Preperation

In [ ]:
from fastai import *
from fastai.vision import *
from fastai.metrics import error_rate

In [ ]:
from google.colab.patches import cv2_imshow

In [ ]:
import cv2
import PIL
import numpy as np
import os
import glob
import pickle
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing.label import _encode
from sklearn import preprocessing # for normaliztion
#from sklearn.model_selection import GridSearchCV #fine tunnig parameters of the models
#import parfit.parfit as pf #fine tunning hyperparameters
#from sklearn.model_selection import ParameterGrid

/usr/local/lib/python3.6/dist-packages/sklearn/utils/deprecation.py:144: FutureWarning: The sklearn.preprocessing.label module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.preprocessing. Anything that cannot be imported from sklearn.preprocessing is now part of the private API.
  warnings.warn(message, FutureWarning)


In [ ]:
import skimage
import skimage.feature as sk
from skimage.feature import local_binary_pattern, greycomatrix, greycoprops
from skimage.filters import gabor
from skimage.feature import hog

In [ ]:
from sklearn import svm
from sklearn.svm import LinearSVC,SVC
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier, BaggingClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.linear_model import Perceptron
from sklearn.linear_model import SGDClassifier 
from sklearn.linear_model import LogisticRegression

In [ ]:
from sklearn.metrics import classification_report # table of precision, recall,F1
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score,f1_score, recall_score, precision_score, roc_curve, auc

In [ ]:
!pip install mahotas

In [ ]:
import mahotas as mt
import mahotas.features as mh_features

In [ ]:
folderSplit = str(0)
basepath = Path("DataSet7/data"); basepath
path = os.path.join(basepath,'360',folderSplit) 
print(path)

DataSet7/data/360/0


**Co-occurance matrix**



In [ ]:
def getGLCMFeatures(gCoMat):
    contrast = sk.greycoprops(gCoMat, prop='contrast')
    dissimilarity = sk.greycoprops(gCoMat, prop='dissimilarity')
    homogeneity = sk.greycoprops(gCoMat, prop='homogeneity')
    energy = sk.greycoprops(gCoMat, prop='energy')
    correlation = sk.greycoprops(gCoMat, prop='correlation')
    print('Contrast = '+str(contrast[0][0]))
    print('Dissimilarity = '+str(dissimilarity[0][0]))
    print('Homogeneity = '+str(homogeneity[0][0]))
    print('Energy = '+str(energy[0][0]))
    print('Correlation = '+str(correlation[0][0]))
    return contrast,dissimilarity,homogeneity,energy,correlation

In [ ]:
def getGLCMFullFeatures(image,distance):
  textures_full_haralick = mt.features.haralick(image, distance=distance)
  #print(textures_full_haralick)
  haralick_labels = ["Angular Second Moment",
                   "Contrast",
                   "Correlation",
                   "Sum of Squares: Variance",
                   "Inverse Difference Moment",
                   "Sum Average",
                   "Sum Variance",
                   "Sum Entropy",
                   "Entropy",
                   "Difference Variance",
                   "Difference Entropy",
                   "Information Measure of Correlation 1",
                   "Information Measure of Correlation 2"]  #,
                   #"Maximal Correlation Coefficient (Not return by default as not stable)"]
        
        #print('mahotas, haralick:')
  for i in range(len(haralick_labels)):
        print('{}: {}:{}'.format(i, haralick_labels[i], textures_full_haralick[0][i]))

**LBP**

In [ ]:
# Finding LBP
def calcLBP(image,points, readios):
  features_lbp = local_binary_pattern(image,points,readios,'uniform') #Radius = 1, No. of neighbours = 8
  features_lbp = np.uint8((features_lbp/features_lbp.max())*255) #Converting to unit8
  return features_lbp

In [ ]:
def calcFeatreusOFLBP(features_lbp):
  # Energy and Entropy of LBP feature
  lbp_hist,_ = np.histogram(features_lbp,8)
  lbp_hist = np.array(lbp_hist,dtype=float)
  lbp_prob = np.divide(lbp_hist,np.sum(lbp_hist))
  lbp_energy = np.sum(lbp_prob**2)
  lbp_entropy = -np.sum(np.multiply(lbp_prob,np.log2(lbp_prob)))
  print('LBP energy = '+str(lbp_energy))
  print('LBP entropy = '+str(lbp_entropy))
  return lbp_energy,lbp_entropy

# **GLCM**

In [ ]:
def extract_GLCM_features(image, distance):        
        # calculate haralick texture features for 4 types of adjacency
        #print('------')
        #textures = mt.features.haralick(image, distance=distance)
        #print('1. extract_GLCM_features, Extract all haralick features...')
        textures_full_haralick = mt.features.haralick(image, distance=distance)[0] #only 0 angle
        haralick_labels = ["Angular Second Moment",
                   "Contrast",
                   "Correlation",
                   "Sum of Squares: Variance",
                   "Inverse Difference Moment",
                   "Sum Average",
                   "Sum Variance",
                   "Sum Entropy",
                   "Entropy",
                   "Difference Variance",
                   "Difference Entropy",
                   "Information Measure of Correlation 1",
                   "Information Measure of Correlation 2"]  #,
                   #"Maximal Correlation Coefficient (Not return by default as not stable)"]

        glcm = sk.greycomatrix(image, distances=[distance], angles=[0], levels=256, symmetric=True, normed=True) # Co-occurance matrix
         
        #print('3. extract_GLCM_features, calculate greycoprops for specific features')
        features_glcm = []
        features_glcm_text = []
        props = ['contrast', 'correlation','ASM', 'dissimilarity', 'homogeneity', 'energy']
        angelIndex = 0 # 0 angel
        for f in props:
          feature_value = sk.greycoprops(glcm, f)[angelIndex,0] 
          features_glcm.append(feature_value)
          features_glcm_text.append('skimage. {}: {}'.format(f, feature_value))

        features_glcm = np.array(features_glcm) 
        #return ht_mean
        return textures_full_haralick, features_glcm

In [ ]:
def extractGLCMFeaturesFromFiles(paths, distance):
  # empty list to hold feature vectors and train labels
  _features = []
  _full_features = []
  _labels = []

  # loop over the training dataset
  print ("[STATUS] Started extracting haralick textures..")
  #for train_name in train_names:
  for path in paths:
          cur_path = str(path) 
          
          cur_label =  os.path.basename(os.path.dirname(cur_path)) #get directory name 
             
          #print ("Processing Image -  in {}".format( cur_path))
          # read the training image
          grayImage = cv2.imread(str(cur_path),0)         
          full_features, features = extract_GLCM_features(grayImage, distance)
          #print(features.shape)
          # append the feature vector and label
          _features.append(features)
          _full_features.append(full_features)
          _labels.append(cur_label)

  return _full_features, _features , _labels

In [ ]:
# Finding LBP
def calc_LBP_features(image,points, readios):
  features_lbp = local_binary_pattern(image,points,readios,'uniform') #Radius = 1, No. of neighbours = 8
  features_lbp = np.uint8((features_lbp/features_lbp.max())*255) #Converting to unit8
  return features_lbp

# **LBP**

In [ ]:
def extract_LBP_features(image, neighbours_points, radios):
  # Finding LBP
  METHOD = 'uniform'
  features_lbp = local_binary_pattern(image, neighbours_points, radios,METHOD) #Example Radius = 1 or 3, No. of neighbours = 8
  features_lbp = np.uint8((features_lbp/features_lbp.max())*255) #Converting to unit8
  
  # Energy and Entropy of LBP feature
  lbp_hist,_ = np.histogram(features_lbp,8) #should be neighbours_points? *** no, it should be the nubmer of colors im image **255**
  lbp_hist = np.array(lbp_hist,dtype=float)
  lbp_prob = np.divide(lbp_hist,np.sum(lbp_hist))
  lbp_energy = np.sum(lbp_prob**2)
  lbp_entropy = -np.sum(np.multiply(lbp_prob,np.log2(lbp_prob)))
  #print('LBP energy = '+str(lbp_energy))
  #print('LBP entropy = '+str(lbp_entropy))
  return [lbp_energy,lbp_entropy], features_lbp

In [ ]:
def extractLBPFeaturesFromFiles(paths, points, radios):
  # empty list to hold feature vectors and train labels
  _features = []
  _features_lbp = [] 
  _labels = []

  # loop over the training dataset
  print ("[STATUS] Started extracting LBP textures..")
  #for train_name in train_names:
  for path in paths:
          cur_path = str(path) 
          
          cur_label =  os.path.basename(os.path.dirname(cur_path)) #get directory name 
             
          #print ("Processing Image -  in {} points: {} radios: {}".format( cur_path, points, radios))
          # read the training image
          grayImage = cv2.imread(str(cur_path),0)
          features, features_lbp = extract_LBP_features(grayImage, points, radios)
          #print(features.shape)
          # append the feature vector and label
          _features_lbp.append(features_lbp)
          _features.append(features)
          _labels.append(cur_label)

  return _features, _features_lbp , _labels

# Load Features

In [ ]:
 def loadFeatures(fileName):
    file = open(fileName, 'rb')
    data = pickle.load(file)
    return data

In [ ]:
glcm_f = loadFeatures("glcm_features_us_ds7_360_folder0.pckl")
#LBP_glcm_f = loadFeatures("lbp_glcm_features_us_ds7_360_folder0.pckl")
LBP_f = loadFeatures("LBP_features_us_ds7_360_folder0.pckl")
Gabor_f = loadFeatures("Gabor_features_us_ds7_360_folder0.pckl")

In [ ]:
glcm_f = loadFeatures("glcm_features_us_ds7_360_folder0.pckl")

In [ ]:
LBP_f = loadFeatures("LBP_features_us_ds7_360_folder0.pckl")

In [ ]:
distance = 0
f= glcm_f[distance]["train"]["features"]
fn= glcm_f[distance]["train"]["features_normalized"]
l=glcm_f[distance]['train']['categorial_labels']
print('features',f)
print('train_features_normalized',fn)
#print('categorial_labels',l)
ft= glcm_f[distance]["test"]["features"]
ftn= glcm_f[distance]['test']['full_features_normalized']
lt=glcm_f[distance]['test']['categorial_labels']
print('full_features_normalized',ftn)
#print(ft)
#print(lt)

features [array([0.      , 1.      , 0.017359, 0.      , 1.      , 0.131754]), array([0.      , 1.      , 0.164917, 0.      , 1.      , 0.4061  ]), array([0.      , 1.      , 0.12823 , 0.      , 1.      , 0.358092]), array([0.      , 1.      , 0.145892, 0.      , 1.      , 0.381958]), array([0.      , 1.      , 0.132219, 0.      , 1.      , 0.363619]), array([0.      , 1.      , 0.135041, 0.      , 1.      , 0.36748 ]), array([0.      , 1.      , 0.029443, 0.      , 1.      , 0.17159 ]), array([0.      , 1.      , 0.065201, 0.      , 1.      , 0.255345]), array([0.      , 1.      , 0.114095, 0.      , 1.      , 0.33778 ]), array([0.      , 1.      , 0.115859, 0.      , 1.      , 0.34038 ]), array([0.      , 1.      , 0.025064, 0.      , 1.      , 0.158315]), array([0.      , 1.      , 0.121534, 0.      , 1.      , 0.348617]), array([0.      , 1.      , 0.143398, 0.      , 1.      , 0.378679]), array([0.      , 1.      , 0.121837, 0.      , 1.      , 0.349051]), array([0.      , 1.     

# Test Models

In [ ]:
def trainClassifier(train_features, train_labels, model):
  features = np.array(train_features)
  model.fit(features, train_labels) 
  return model

In [ ]:
def testModel(model, test_features, labels):
  prediction = model.predict(test_features)  
  pred_data = labels
  test_labels = prediction
  print("F1: " + str(f1_score(test_labels, pred_data, average='micro')))
  print("F1_macro: " + str(f1_score(test_labels, pred_data, average='macro')))
  print("Recall: " + str(recall_score(test_labels, pred_data, average='micro')))
  print("Recall_macro: " + str(recall_score(test_labels, pred_data, average='macro')))
  print("Precision: " + str(precision_score(test_labels, pred_data, average='micro')))
  print("Precision_macro: " + str(precision_score(test_labels, pred_data, average='macro')))
  print("Accuracy:" + str(accuracy_score(test_labels, pred_data)))
  print("-----------------------------------------");
  acc = accuracy_score(prediction, labels)
  return acc

# Train and Predict GLCM

# Optimization

In [ ]:
def getGlcmFearturesAndLabels(distance):
    train_features= glcm_f[distance]["train"]["features"]
    train_features_normalized= glcm_f[distance]["train"]["features_normalized"]
    train_labels_categorial=glcm_f[distance]['train']['categorial_labels']

    test_features= glcm_f[distance]["test"]["features"]
    test_features_normalized= glcm_f[distance]["test"]["features_normalized"]

    train_full_features =  glcm_f[distance]["train"]["full_features"]
    train_full_features_normalized =  glcm_f[distance]["train"]["full_features_normalized"]

    test_full_features =  glcm_f[distance]["test"]["full_features"]
    test_full_features_normalized =  glcm_f[distance]["test"]["full_features_normalized"]

    test_labels_categorial=glcm_f[distance]['test']['categorial_labels']

    return   train_full_features, train_full_features_normalized, train_features, train_features_normalized , train_labels_categorial, test_full_features, test_full_features_normalized, test_features, test_features_normalized, test_labels_categorial

In [ ]:
distance = 18
train_full_features, train_full_features_normalized, train_features, train_features_normalized , train_labels_categorial, test_full_features, test_full_features_normalized, test_features, test_features_normalized, test_labels_categorial = getGlcmFearturesAndLabels(distance)

In [ ]:
!pip install optuna

     |████████████████████████████████| 235kB 9.2MB/s 
     |████████████████████████████████| 1.1MB 29.4MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 81kB 9.6MB/s 
     |████████████████████████████████| 81kB 9.1MB/s 
     |████████████████████████████████| 112kB 47.6MB/s 
     |████████████████████████████████| 133kB 49.7MB/s 
     |████████████████████████████████| 51kB 7.2MB/s 
  Created wheel for alembic: filename=alembic-1.4.2-cp36-none-any.whl size=159543 sha256=92ed2feab30acf0bf2100e05cd34bfe6cddfe97a46384291850afaaca3bbe9e9
  Stored in directory: /root/.cache/pip/wheels/1f/04/83/76023f7a4c14688c0b5c2682a96392cfdd3ee4449eaaa287ef
Successfully built alembic
  Created wheel for optuna: filename=optuna-2.0.0-cp36-none-any.whl size=312964 sha256=54c9840da73afe9646df283e0755873e6ec2a12dcd0f2d202ed5484b0843c840
  Stored in directory: /root/.cache/pip/wheels/b5

In [ ]:
import optuna

In [ ]:
def startRfModelobjective(trial):
    distance = None
    return startRf(trial, distance)    

In [ ]:
def startRfModelobjective_distance4(trial):
    distance = 4
    return startRf(trial, distance)

In [ ]:
def startRf(trial, distance):
    #try:  
        if distance == None:      
          distance = trial.suggest_int('distance', 0, 20)                          
        #distance = 4
        
        train_full_features, train_full_features_normalized, train_features, train_features_normalized , train_labels_categorial, test_full_features, test_full_features_normalized, test_features, test_features_normalized, test_labels_categorial = getGlcmFearturesAndLabels(distance)
        rf_max_depth = trial.suggest_int('rf_max_depth', 2, 100)  # max_depth represents the depth of each tree in the forest
        rf_n_estimators = trial.suggest_int('n_estimators', 10, 1000)  #n_estimators represents the number of trees in the forest.
        rf_min_samples_splits  = trial.suggest_int('rf_min_samples_splits', 2, 10)
        apply_Entropy = trial.suggest_categorical("apply_Entropy", [True, False])

        model = RandomForestClassifier(n_estimators=rf_n_estimators, max_depth=rf_max_depth, min_samples_split = rf_min_samples_splits , random_state=0, criterion='entropy' if apply_Entropy else 'gini')


        apply_fullFeatures = trial.suggest_categorical("apply_fullFeatures", [True, False])
        apply_NormalizedFeatures = trial.suggest_categorical("apply_NormalizedFeatures", [True, False])

        print('----------------------------')
        print("hyperparameters: {}".format(trial.params))
        modelName = 'RandomForestClassifier'
    
        if apply_fullFeatures:     
            print('1. train ', modelName)        
            modelFited = trainClassifier(np.array(train_full_features_normalized if apply_NormalizedFeatures else train_full_features), train_labels_categorial, model)
            print('2. test ',modelName)
            acc = testModel(modelFited, np.array(test_full_features_normalized if apply_NormalizedFeatures else test_full_features) ,test_labels_categorial)
        else:  #features
            print('1. train ', modelName)
            modelFited = trainClassifier(np.array(train_features_normalized if apply_NormalizedFeatures else train_features), train_labels_categorial, model)
            print('2. test ',modelName)
            acc = testModel(modelFited, np.array(test_features if apply_NormalizedFeatures else test_features_normalized) ,test_labels_categorial)           
    #except: 
    #  acc = 0
    #return acc
        return acc

In [ ]:
def startKnnModelobjectiveGLCM(trial):
    distance = None
    return startKnnModelobjective(trial, distance)

In [ ]:
def startKnnModelobjectiveGLCM_Distance3(trial):
    distance = 3
    return startKnnModelobjective(trial, distance)

In [ ]:
def startKnnModelobjective(trial, distance):
    #try:
        if distance == None:      
          distance = trial.suggest_int('distance', 0, 20)         
        #distance = 3
        #distance = 2
        #distance = 4
        #distance = 21
        train_full_features, train_full_features_normalized, train_features, train_features_normalized , train_labels_categorial, test_full_features, test_full_features_normalized, test_features, test_features_normalized, test_labels_categorial = getGlcmFearturesAndLabels(distance)
        knn_n_neighbors = trial.suggest_int('knn_n_neighbors', 2, 150)  # max_depth represents the depth of each tree in the forest
        knn_leaf_size = trial.suggest_int('knn_leaf_size', 1, 500)  #n_estimators represents the number of trees in the forest.        
        algo = trial.suggest_categorical("algo", ["auto", "ball_tree","kd_tree","brute"])
        knn_weights = trial.suggest_categorical("knn_weights", ["uniform", "distance"])
        knn_metric = trial.suggest_categorical("knn_metric", ["minkowski", "chebyshev"])
        model = KNeighborsClassifier(n_neighbors=knn_n_neighbors, algorithm=algo)

        apply_fullFeatures = trial.suggest_categorical("apply_fullFeatures", [True, False])
        apply_NormalizedFeatures = trial.suggest_categorical("apply_NormalizedFeatures", [True, False])

        print('----------------------------')
        print("hyperparameters: {}".format(trial.params))
        modelName = 'knn'
    
        if apply_fullFeatures:     
            print('1. train ', modelName)        
            modelFited = trainClassifier(np.array(train_full_features_normalized if apply_NormalizedFeatures else train_full_features), train_labels_categorial, model)
            print('2. test ',modelName)
            acc = testModel(modelFited, np.array(test_full_features_normalized if apply_NormalizedFeatures else test_full_features) ,test_labels_categorial)
        else:  #features
            print('1. train ', modelName)
            modelFited = trainClassifier(np.array(train_features_normalized if apply_NormalizedFeatures else train_features), train_labels_categorial, model)
            print('2. test ',modelName)
            acc = testModel(modelFited, np.array(test_features if apply_NormalizedFeatures else test_features_normalized) ,test_labels_categorial)           
    #except: 
    #  acc = 0
    #return acc
        return acc

In [ ]:
import xgboost as xgb

In [ ]:
def startxgboostModelobjectiveGLCM(trial):
    distance = None
    return startxgboostGLCM(trial, distance)

In [ ]:
def startxgboostModelobjectiveGLCMDistance9(trial):
    distance = 9
    return startxgboostGLCM(trial, distance)

In [ ]:
def startxgboostModelobjectiveGLCMDistance12(trial):
    distance = 12
    return startxgboostGLCM(trial, distance)

In [ ]:
def startxgboostGLCM(trial, distance):
        if distance == None:      
          distance = trial.suggest_int('distance', 0, 20)       

        train_full_features, train_full_features_normalized, train_features, train_features_normalized , train_labels_categorial, test_full_features, test_full_features_normalized, test_features, test_features_normalized, test_labels_categorial = getGlcmFearturesAndLabels(distance)
        
        param = {
        "silent": 1,
        "objective": "binary:logistic",
        "eval_metric": "auc",
        "booster": trial.suggest_categorical("booster", ["gbtree", "gblinear", "dart"]),
        "lambda": trial.suggest_float("lambda", 1e-8, 1.0, log=True),
        "alpha": trial.suggest_float("alpha", 1e-8, 1.0, log=True),
        }

        if param["booster"] == "gbtree" or param["booster"] == "dart":
            param["max_depth"] = trial.suggest_int("max_depth", 1, 9)
            param["eta"] = trial.suggest_float("eta", 1e-8, 1.0, log=True)
            param["gamma"] = trial.suggest_float("gamma", 1e-8, 1.0, log=True)
            param["grow_policy"] = trial.suggest_categorical("grow_policy", ["depthwise", "lossguide"])
        if param["booster"] == "dart":
            param["sample_type"] = trial.suggest_categorical("sample_type", ["uniform", "weighted"])
            param["normalize_type"] = trial.suggest_categorical("normalize_type", ["tree", "forest"])
            param["rate_drop"] = trial.suggest_float("rate_drop", 1e-8, 1.0, log=True)
            param["skip_drop"] = trial.suggest_float("skip_drop", 1e-8, 1.0, log=True)


        # Add a callback for pruning.
        pruning_callback = optuna.integration.XGBoostPruningCallback(trial, "validation-auc")

        apply_fullFeatures = trial.suggest_categorical("apply_fullFeatures", [True, False])
        apply_NormalizedFeatures = trial.suggest_categorical("apply_NormalizedFeatures", [True, False])

        print('----------------------------')
        print("hyperparameters: {}".format(trial.params))
        modelName = 'xgboost'
    
        if apply_fullFeatures:     
            print('1. train ', modelName) 
            dtrain = xgb.DMatrix(np.array(train_full_features_normalized if apply_NormalizedFeatures else train_full_features), label=train_labels_categorial)
            dvalid = xgb.DMatrix(np.array(test_full_features_normalized if apply_NormalizedFeatures else test_full_features), label=test_labels_categorial)       
            modelFited = xgb.train(param, dtrain, evals=[(dvalid, "validation")], callbacks=[pruning_callback])
            print('2. test ',modelName)
            preds = modelFited.predict(dvalid)
            pred_labels = np.rint(preds)
            acc = accuracy_score(test_labels_categorial, pred_labels)
        else:  #features
            print('1. train ', modelName)
            dtrain = xgb.DMatrix(np.array(train_features_normalized if apply_NormalizedFeatures else train_features), label=train_labels_categorial)
            dvalid = xgb.DMatrix(np.array(test_features if apply_NormalizedFeatures else test_features_normalized), label=test_labels_categorial)   
            modelFited = xgb.train(param, dtrain, evals=[(dvalid, "validation")], callbacks=[pruning_callback])
            print('2. test ',modelName)
            preds = modelFited.predict(dvalid)
            pred_labels = np.rint(preds)
            acc = accuracy_score(test_labels_categorial, pred_labels)

        test_labels = test_labels_categorial
        pred_data = pred_labels
        print("F1: " + str(f1_score(test_labels, pred_data, average='micro')))
        print("F1_macro: " + str(f1_score(test_labels, pred_data, average='macro')))
        print("Recall: " + str(recall_score(test_labels, pred_data, average='micro')))
        print("Recall_macro: " + str(recall_score(test_labels, pred_data, average='macro')))
        print("Precision: " + str(precision_score(test_labels, pred_data, average='micro')))
        print("Precision_macro: " + str(precision_score(test_labels, pred_data, average='macro')))               
    #except: 
    #  acc = 0
    #return acc
        print('Accuarcy: ', acc)
        return acc

All distance

In [ ]:
study = optuna.create_study(direction='maximize')  # Create a new study.
study.optimize(startRfModelobjective, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {}".format(trial.params))

----------------------------
hyperparameters: {'distance': 15, 'rf_max_depth': 92, 'n_estimators': 891, 'rf_min_samples_splits': 5, 'apply_Entropy': True, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.45054945054945056
F1_macro: 0.3106060606060606
Recall: 0.45054945054945056


/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning:

Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.



Recall_macro: 0.22527472527472528
Precision: 0.45054945054945056
Precision_macro: 0.5
Accuracy:0.45054945054945056
-----------------------------------------


[I 2020-08-22 18:51:10,536] Trial 0 finished with value: 0.45054945054945056 and parameters: {'distance': 15, 'rf_max_depth': 92, 'n_estimators': 891, 'rf_min_samples_splits': 5, 'apply_Entropy': True, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}. Best is trial 0 with value: 0.45054945054945056.


----------------------------
hyperparameters: {'distance': 0, 'rf_max_depth': 67, 'n_estimators': 655, 'rf_min_samples_splits': 3, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.5494505494505495
F1_macro: 0.5494505494505494
Recall: 0.5494505494505495
Recall_macro: 0.5548780487804879
Precision: 0.5494505494505495
Precision_macro: 0.5548780487804879
Accuracy:0.5494505494505495
-----------------------------------------


...

----------------------------
hyperparameters: {'distance': 6, 'rf_max_depth': 82, 'n_estimators': 851, 'rf_min_samples_splits': 8, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6648351648351648
F1_macro: 0.6643386243386242
Recall: 0.6648351648351648
Recall_macro: 0.6660021747009786
Precision: 0.6648351648351648
Precision_macro: 0.667560975609756
Accuracy:0.6648351648351648
-----------------------------------------


[I 2020-08-22 18:58:18,943] Trial 298 finished with value: 0.6648351648351648 and parameters: {'distance': 6, 'rf_max_depth': 82, 'n_estimators': 851, 'rf_min_samples_splits': 8, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}. Best is trial 241 with value: 0.6703296703296703.


----------------------------
hyperparameters: {'distance': 5, 'rf_max_depth': 78, 'n_estimators': 862, 'rf_min_samples_splits': 9, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6483516483516484
F1_macro: 0.6472868217054264
Recall: 0.6483516483516484
Recall_macro: 0.6478260869565218
Precision: 0.6483516483516484
Precision_macro: 0.6492682926829269
Accuracy:0.6483516483516484
-----------------------------------------


[I 2020-08-22 18:58:20,512] Trial 299 finished with value: 0.6483516483516484 and parameters: {'distance': 5, 'rf_max_depth': 78, 'n_estimators': 862, 'rf_min_samples_splits': 9, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}. Best is trial 241 with value: 0.6703296703296703.


Best hyperparameters: {'distance': 6, 'rf_max_depth': 72, 'n_estimators': 767, 'rf_min_samples_splits': 8, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}


In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'distance': 6, 'rf_max_depth': 72, 'n_estimators': 767, 'rf_min_samples_splits': 8, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False} accuracy:0.6703296703296703


Distance = 2

In [ ]:
study = optuna.create_study(direction='maximize')  # Create a new study.
study.optimize(startRfModelobjective, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {}".format(trial.params))

----------------------------
hyperparameters: {'rf_max_depth': 62, 'n_estimators': 452, 'rf_min_samples_splits': 4, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6153846153846154
F1_macro: 0.6137052759248028
Recall: 0.6153846153846154
Recall_macro: 0.6138781431334623
Precision: 0.6153846153846154
Precision_macro: 0.6148780487804878
Accuracy:0.6153846153846154
-----------------------------------------


[I 2020-08-22 16:54:00,313] Trial 0 finished with value: 0.6153846153846154 and parameters: {'rf_max_depth': 62, 'n_estimators': 452, 'rf_min_samples_splits': 4, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}. Best is trial 0 with value: 0.6153846153846154.


----------------------------
hyperparameters: {'rf_max_depth': 18, 'n_estimators': 531, 'rf_min_samples_splits': 6, 'apply_Entropy': False, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.5494505494505495
F1_macro: 0.3546099290780142
Recall: 0.5494505494505495


/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning:

Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.



Recall_macro: 0.27472527472527475
Precision: 0.5494505494505495
Precision_macro: 0.5
Accuracy:0.5494505494505495
-----------------------------------------


...

----------------------------
hyperparameters: {'rf_max_depth': 31, 'n_estimators': 691, 'rf_min_samples_splits': 2, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6428571428571429
F1_macro: 0.6419816602608722
Recall: 0.6428571428571429
Recall_macro: 0.6428571428571428
Precision: 0.6428571428571429
Precision_macro: 0.6442682926829268
Accuracy:0.6428571428571429
-----------------------------------------


[I 2020-08-22 17:01:34,474] Trial 298 finished with value: 0.6428571428571429 and parameters: {'rf_max_depth': 31, 'n_estimators': 691, 'rf_min_samples_splits': 2, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}. Best is trial 29 with value: 0.6428571428571429.


----------------------------
hyperparameters: {'rf_max_depth': 56, 'n_estimators': 635, 'rf_min_samples_splits': 2, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6428571428571429
F1_macro: 0.6419816602608722
Recall: 0.6428571428571429
Recall_macro: 0.6428571428571428
Precision: 0.6428571428571429
Precision_macro: 0.6442682926829268
Accuracy:0.6428571428571429
-----------------------------------------


[I 2020-08-22 17:01:36,009] Trial 299 finished with value: 0.6428571428571429 and parameters: {'rf_max_depth': 56, 'n_estimators': 635, 'rf_min_samples_splits': 2, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}. Best is trial 29 with value: 0.6428571428571429.


Best hyperparameters: {'rf_max_depth': 27, 'n_estimators': 559, 'rf_min_samples_splits': 2, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}


In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'rf_max_depth': 27, 'n_estimators': 559, 'rf_min_samples_splits': 2, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False} accuracy:0.6428571428571429


RF Distance = 4

In [ ]:
study = optuna.create_study(direction='maximize')  # Create a new study.
study.optimize(startRfModelobjective, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

----------------------------
hyperparameters: {'rf_max_depth': 9, 'n_estimators': 405, 'rf_min_samples_splits': 2, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.5714285714285714
F1_macro: 0.5688775510204082
Recall: 0.5714285714285714
Recall_macro: 0.5896542827657378
Precision: 0.5714285714285714
Precision_macro: 0.5847560975609756
Accuracy:0.5714285714285714
-----------------------------------------


[I 2020-08-22 17:19:44,606] Trial 0 finished with value: 0.5714285714285714 and parameters: {'rf_max_depth': 9, 'n_estimators': 405, 'rf_min_samples_splits': 2, 'apply_Entropy': True, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}. Best is trial 0 with value: 0.5714285714285714.


----------------------------
hyperparameters: {'rf_max_depth': 46, 'n_estimators': 121, 'rf_min_samples_splits': 6, 'apply_Entropy': True, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.5494505494505495
F1_macro: 0.3546099290780142
Recall: 0.5494505494505495


/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning:

Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.



Recall_macro: 0.27472527472527475
Precision: 0.5494505494505495
Precision_macro: 0.5
Accuracy:0.5494505494505495
-----------------------------------------


...

Recall_macro: 0.27472527472527475
Precision: 0.5494505494505495
Precision_macro: 0.5
Accuracy:0.5494505494505495
-----------------------------------------


[I 2020-08-22 17:22:19,889] Trial 298 finished with value: 0.5494505494505495 and parameters: {'rf_max_depth': 8, 'n_estimators': 41, 'rf_min_samples_splits': 9, 'apply_Entropy': False, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': False}. Best is trial 295 with value: 0.6758241758241759.


----------------------------
hyperparameters: {'rf_max_depth': 21, 'n_estimators': 10, 'rf_min_samples_splits': 7, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6098901098901099
F1_macro: 0.6072221040153196
Recall: 0.6098901098901099
Recall_macro: 0.6070952092177078
Precision: 0.6098901098901099
Precision_macro: 0.6076829268292683
Accuracy:0.6098901098901099
-----------------------------------------


[I 2020-08-22 17:22:20,006] Trial 299 finished with value: 0.6098901098901099 and parameters: {'rf_max_depth': 21, 'n_estimators': 10, 'rf_min_samples_splits': 7, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}. Best is trial 295 with value: 0.6758241758241759.


Best hyperparameters: {'rf_max_depth': 15, 'n_estimators': 37, 'rf_min_samples_splits': 8, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False} accuracy:0.6758241758241759


In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'rf_max_depth': 15, 'n_estimators': 37, 'rf_min_samples_splits': 8, 'apply_Entropy': False, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False} accuracy:0.6758241758241759


KNN

In [ ]:
study = optuna.create_study(direction='maximize')  # Create a new study.
study.optimize(startKnnModelobjectiveGLCM, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

----------------------------
hyperparameters: {'distance': 16, 'knn_n_neighbors': 53, 'knn_leaf_size': 86, 'algo': 'brute', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.46703296703296704
F1_macro: 0.4668881171674467
Recall: 0.46703296703296704
Recall_macro: 0.4701637355973317
Precision: 0.46703296703296704
Precision_macro: 0.47
Accuracy:0.46703296703296704
-----------------------------------------


[I 2020-08-22 17:44:40,718] Trial 0 finished with value: 0.46703296703296704 and parameters: {'distance': 16, 'knn_n_neighbors': 53, 'knn_leaf_size': 86, 'algo': 'brute', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}. Best is trial 0 with value: 0.46703296703296704.


----------------------------
hyperparameters: {'distance': 5, 'knn_n_neighbors': 148, 'knn_leaf_size': 465, 'algo': 'brute', 'knn_weights': 'uniform', 'knn_metric': 'chebyshev', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.5714285714285714
F1_macro: 0.5625
Recall: 0.5714285714285714
Recall_macro: 0.6061507936507937
Precision: 0.5714285714285714
Precision_macro: 0.5913414634146341
Accuracy:0.5714285714285714
-----------------------------------------


[I 2020-08-22 17:44:40,797] Trial 1 finished with value: 0.5714285714285714 and parameters: {'distance': 5, 'knn_n_neighbors': 148, 'knn_leaf_size': 465, 'algo': 'brute', 'knn_weights': 'uniform', 'knn_metric': 'chebyshev', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}. Best is trial 1 with value: 0.5714285714285714.


----------------------------
hyperparameters: {'distance': 19, 'knn_n_neighbors': 44, 'knn_leaf_size': 205, 'algo': 'brute', 'knn_weights': 'distance', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.45054945054945056
F1_macro: 0.3106060606060606
Recall: 0.45054945054945056


...

----------------------------
hyperparameters: {'distance': 3, 'knn_n_neighbors': 143, 'knn_leaf_size': 285, 'algo': 'ball_tree', 'knn_weights': 'distance', 'knn_metric': 'chebyshev', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6483516483516484
F1_macro: 0.6468162522741056
Recall: 0.6483516483516484
Recall_macro: 0.6468810444874276
Precision: 0.6483516483516484
Precision_macro: 0.6481707317073171
Accuracy:0.6483516483516484
-----------------------------------------


[I 2020-08-22 17:45:14,176] Trial 298 finished with value: 0.6483516483516484 and parameters: {'distance': 3, 'knn_n_neighbors': 143, 'knn_leaf_size': 285, 'algo': 'ball_tree', 'knn_weights': 'distance', 'knn_metric': 'chebyshev', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}. Best is trial 46 with value: 0.6593406593406593.


----------------------------
hyperparameters: {'distance': 4, 'knn_n_neighbors': 139, 'knn_leaf_size': 308, 'algo': 'brute', 'knn_weights': 'distance', 'knn_metric': 'chebyshev', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6428571428571429
F1_macro: 0.6425873893471102
Recall: 0.6428571428571429
Recall_macro: 0.6453115547489413
Precision: 0.6428571428571429
Precision_macro: 0.6464634146341464
Accuracy:0.6428571428571429
-----------------------------------------


[I 2020-08-22 17:45:14,264] Trial 299 finished with value: 0.6428571428571429 and parameters: {'distance': 4, 'knn_n_neighbors': 139, 'knn_leaf_size': 308, 'algo': 'brute', 'knn_weights': 'distance', 'knn_metric': 'chebyshev', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}. Best is trial 46 with value: 0.6593406593406593.


Best hyperparameters: {'distance': 3, 'knn_n_neighbors': 144, 'knn_leaf_size': 336, 'algo': 'brute', 'knn_weights': 'distance', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True} accuracy:0.6593406593406593


In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'distance': 3, 'knn_n_neighbors': 144, 'knn_leaf_size': 336, 'algo': 'brute', 'knn_weights': 'distance', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True} accuracy:0.6593406593406593


KNN distance =3 

In [ ]:
study = optuna.create_study(direction='maximize')  # Create a new study.
study.optimize(startKnnModelobjectiveGLCM_Distance3, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

----------------------------
hyperparameters: {'knn_n_neighbors': 98, 'knn_leaf_size': 353, 'algo': 'auto', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.5604395604395604
F1_macro: 0.5578231292517006
Recall: 0.5604395604395604
Recall_macro: 0.5779153766769867
Precision: 0.5604395604395604
Precision_macro: 0.5736585365853658
Accuracy:0.5604395604395604
-----------------------------------------


[I 2020-08-22 17:49:48,021] Trial 0 finished with value: 0.5604395604395604 and parameters: {'knn_n_neighbors': 98, 'knn_leaf_size': 353, 'algo': 'auto', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}. Best is trial 0 with value: 0.5604395604395604.


----------------------------
hyperparameters: {'knn_n_neighbors': 12, 'knn_leaf_size': 421, 'algo': 'brute', 'knn_weights': 'uniform', 'knn_metric': 'chebyshev', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.510989010989011
F1_macro: 0.5076446092586401
Recall: 0.510989010989011
Recall_macro: 0.5077622801697999
Precision: 0.510989010989011
Precision_macro: 0.5078048780487805
Accuracy:0.510989010989011
-----------------------------------------


[I 2020-08-22 17:49:48,117] Trial 1 finished with value: 0.510989010989011 and parameters: {'knn_n_neighbors': 12, 'knn_leaf_size': 421, 'algo': 'brute', 'knn_weights': 'uniform', 'knn_metric': 'chebyshev', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}. Best is trial 0 with value: 0.5604395604395604.


----------------------------
hyperparameters: {'knn_n_neighbors': 135, 'knn_leaf_size': 422, 'algo': 'brute', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6428571428571429
F1_macro: 0.6425873893471102
Recall: 0.6428571428571429
Recall_macro: 0.6453115547489413
Precision: 0.6428571428571429
Precision_macro: 0.6464634146341464
Accuracy:0.6428571428571429
-----------------------------------------


...

----------------------------
hyperparameters: {'knn_n_neighbors': 145, 'knn_leaf_size': 78, 'algo': 'auto', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6483516483516484
F1_macro: 0.6468162522741056
Recall: 0.6483516483516484
Recall_macro: 0.6468810444874276
Precision: 0.6483516483516484
Precision_macro: 0.6481707317073171
Accuracy:0.6483516483516484
-----------------------------------------


[I 2020-08-22 17:50:16,610] Trial 298 finished with value: 0.6483516483516484 and parameters: {'knn_n_neighbors': 145, 'knn_leaf_size': 78, 'algo': 'auto', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}. Best is trial 43 with value: 0.6593406593406593.


----------------------------
hyperparameters: {'knn_n_neighbors': 147, 'knn_leaf_size': 176, 'algo': 'auto', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  RandomForestClassifier
2. test  RandomForestClassifier
F1: 0.6538461538461539
F1_macro: 0.6520710059171598
Recall: 0.6538461538461539
Recall_macro: 0.651966122202057
Precision: 0.6538461538461539
Precision_macro: 0.6531707317073171
Accuracy:0.6538461538461539
-----------------------------------------


[I 2020-08-22 17:50:16,710] Trial 299 finished with value: 0.6538461538461539 and parameters: {'knn_n_neighbors': 147, 'knn_leaf_size': 176, 'algo': 'auto', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}. Best is trial 43 with value: 0.6593406593406593.


Best hyperparameters: {'knn_n_neighbors': 144, 'knn_leaf_size': 430, 'algo': 'auto', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True} accuracy:0.6593406593406593


In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'knn_n_neighbors': 144, 'knn_leaf_size': 430, 'algo': 'auto', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True} accuracy:0.6593406593406593


XGBoost

In [ ]:
study = optuna.create_study(
        pruner=optuna.pruners.MedianPruner(n_warmup_steps=5), direction="maximize"
    )
study.optimize(startxgboostModelobjectiveGLCM, n_trials=100)
print(study.best_trial)
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

----------------------------
hyperparameters: {'distance': 15, 'booster': 'gbtree', 'lambda': 1.6445642671864537e-07, 'alpha': 5.9358860683601514e-05, 'max_depth': 6, 'eta': 4.1693421701998306e-07, 'gamma': 3.777264408745907e-08, 'grow_policy': 'depthwise', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}
1. train  xgboost
[0]	validation-auc:0.587195
[1]	validation-auc:0.57811
[2]	validation-auc:0.585915
[3]	validation-auc:0.58561
[4]	validation-auc:0.585305
[5]	validation-auc:0.58561
[6]	validation-auc:0.587134
[7]	validation-auc:0.585976
[8]	validation-auc:0.587378
[9]	validation-auc:0.587561
2. test  xgboost
Accuarcy:  0.5879120879120879


[I 2020-08-22 19:26:05,178] Trial 0 finished with value: 0.5879120879120879 and parameters: {'distance': 15, 'booster': 'gbtree', 'lambda': 1.6445642671864537e-07, 'alpha': 5.9358860683601514e-05, 'max_depth': 6, 'eta': 4.1693421701998306e-07, 'gamma': 3.777264408745907e-08, 'grow_policy': 'depthwise', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': False}. Best is trial 0 with value: 0.5879120879120879.


----------------------------
hyperparameters: {'distance': 2, 'booster': 'gblinear', 'lambda': 7.903703822152462e-08, 'alpha': 0.001535555439803258, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': False}
1. train  xgboost
[0]	validation-auc:0.489939
[1]	validation-auc:0.494024
[2]	validation-auc:0.49372
[3]	validation-auc:0.491707
[4]	validation-auc:0.488841
[5]	validation-auc:0.486037
[6]	validation-auc:0.484939
[7]	validation-auc:0.485061
[8]	validation-auc:0.485915
[9]	validation-auc:0.487134
2. test  xgboost
Accuarcy:  0.45054945054945056


[I 2020-08-22 19:26:05,227] Trial 1 finished with value: 0.45054945054945056 and parameters: {'distance': 2, 'booster': 'gblinear', 'lambda': 7.903703822152462e-08, 'alpha': 0.001535555439803258, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': False}. Best is trial 0 with value: 0.5879120879120879.


----------------------------
hyperparameters: {'distance': 11, 'booster': 'gblinear', 'lambda': 7.1032703244572154e-06, 'alpha': 9.87203072830499e-05, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.551524
[1]	validation-auc:0.524878
[2]	validation-auc:0.5
[3]	validation-auc:0.5
[4]	validation-auc:0.5
[5]	validation-auc:0.5
[6]	validation-auc:0.5
[7]	validation-auc:0.5
[8]	validation-auc:0.5
[9]	validation-auc:0.5
2. test  xgboost
Accuarcy:  0.45054945054945056


...

----------------------------
hyperparameters: {'distance': 11, 'booster': 'gbtree', 'lambda': 0.09883816423878933, 'alpha': 2.3844910983715505e-08, 'max_depth': 8, 'eta': 0.09546747133185893, 'gamma': 1.4216149538165123e-07, 'grow_policy': 'depthwise', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.570366
[1]	validation-auc:0.6
[2]	validation-auc:0.605427
[3]	validation-auc:0.603354
[4]	validation-auc:0.609207


[I 2020-08-22 19:26:12,236] Trial 98 pruned. Trial was pruned at iteration 5.


----------------------------
hyperparameters: {'distance': 7, 'booster': 'gbtree', 'lambda': 0.3867728076995817, 'alpha': 2.579750136680787e-07, 'max_depth': 9, 'eta': 0.015594310370666992, 'gamma': 3.7810088887118204e-07, 'grow_policy': 'depthwise', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.583476
[1]	validation-auc:0.583719
[2]	validation-auc:0.581037
[3]	validation-auc:0.579451
[4]	validation-auc:0.593598


[I 2020-08-22 19:26:12,296] Trial 99 pruned. Trial was pruned at iteration 5.


FrozenTrial(number=92, value=0.6648351648351648, datetime_start=datetime.datetime(2020, 8, 22, 19, 26, 11, 665208), datetime_complete=datetime.datetime(2020, 8, 22, 19, 26, 11, 751842), params={'distance': 9, 'booster': 'gbtree', 'lambda': 0.36088169931415276, 'alpha': 3.152415741738991e-08, 'max_depth': 7, 'eta': 0.07165425481487134, 'gamma': 3.883889922833045e-07, 'grow_policy': 'depthwise', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}, distributions={'distance': IntUniformDistribution(high=20, low=0, step=1), 'booster': CategoricalDistribution(choices=('gbtree', 'gblinear', 'dart')), 'lambda': LogUniformDistribution(high=1.0, low=1e-08), 'alpha': LogUniformDistribution(high=1.0, low=1e-08), 'max_depth': IntUniformDistribution(high=9, low=1, step=1), 'eta': LogUniformDistribution(high=1.0, low=1e-08), 'gamma': LogUniformDistribution(high=1.0, low=1e-08), 'grow_policy': CategoricalDistribution(choices=('depthwise', 'lossguide')), 'apply_fullFeatures': CategoricalDistr

In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'distance': 9, 'booster': 'gbtree', 'lambda': 0.36088169931415276, 'alpha': 3.152415741738991e-08, 'max_depth': 7, 'eta': 0.07165425481487134, 'gamma': 3.883889922833045e-07, 'grow_policy': 'depthwise', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True} accuracy:0.6648351648351648


XGBoost Distance 9

In [ ]:

study = optuna.create_study(
        pruner=optuna.pruners.MedianPruner(n_warmup_steps=5), direction="maximize"
    )
study.optimize(startxgboostModelobjectiveGLCMDistance9, n_trials=300)
print(study.best_trial)
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

----------------------------
hyperparameters: {'booster': 'gblinear', 'lambda': 1.16537922155718e-06, 'alpha': 0.0019263940655077597, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.440183
[1]	validation-auc:0.440122
[2]	validation-auc:0.440122
[3]	validation-auc:0.440122
[4]	validation-auc:0.440122
[5]	validation-auc:0.440122
[6]	validation-auc:0.440122
[7]	validation-auc:0.440122
[8]	validation-auc:0.440122
[9]	validation-auc:0.440122
2. test  xgboost
F1: 0.521978021978022
F1_macro: 0.46148352208958265
Recall: 0.521978021978022
Recall_macro: 0.49365853658536585
Precision: 0.521978021978022
Precision_macro: 0.49067599067599066
Accuarcy:  0.521978021978022


[I 2020-08-22 19:54:18,233] Trial 0 finished with value: 0.521978021978022 and parameters: {'booster': 'gblinear', 'lambda': 1.16537922155718e-06, 'alpha': 0.0019263940655077597, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}. Best is trial 0 with value: 0.521978021978022.


----------------------------
hyperparameters: {'booster': 'dart', 'lambda': 6.647826031331901e-08, 'alpha': 8.004137430125568e-05, 'max_depth': 4, 'eta': 0.00016189958285534566, 'gamma': 1.6299860924100647e-05, 'grow_policy': 'lossguide', 'sample_type': 'uniform', 'normalize_type': 'tree', 'rate_drop': 2.0073738735712614e-07, 'skip_drop': 0.17633934498867612, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.5
[1]	validation-auc:0.5
[2]	validation-auc:0.5
[3]	validation-auc:0.5
[4]	validation-auc:0.5
[5]	validation-auc:0.5
[6]	validation-auc:0.5
[7]	validation-auc:0.5
[8]	validation-auc:0.5
[9]	validation-auc:0.5
2. test  xgboost
F1: 0.45054945054945056
F1_macro: 0.3106060606060606
Recall: 0.45054945054945056
Recall_macro: 0.5
Precision: 0.45054945054945056


/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.



Precision_macro: 0.22527472527472528
Accuarcy:  0.45054945054945056


...

----------------------------
hyperparameters: {'booster': 'gbtree', 'lambda': 0.0006939372739329904, 'alpha': 0.06422225418757876, 'max_depth': 7, 'eta': 0.03110327864818402, 'gamma': 0.002934248194107997, 'grow_policy': 'depthwise', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.624024
[1]	validation-auc:0.62561
[2]	validation-auc:0.654634
[3]	validation-auc:0.658537
[4]	validation-auc:0.662683
[5]	validation-auc:0.667073
[6]	validation-auc:0.669573
[7]	validation-auc:0.667622
[8]	validation-auc:0.66811
[9]	validation-auc:0.667561
2. test  xgboost
F1: 0.6428571428571429
F1_macro: 0.6428463605349757
Recall: 0.6428571428571429
Recall_macro: 0.6497560975609755
Precision: 0.6428571428571429
Precision_macro: 0.6501038992788167
Accuarcy:  0.6428571428571429


[I 2020-08-22 19:54:48,772] Trial 298 finished with value: 0.6428571428571429 and parameters: {'booster': 'gbtree', 'lambda': 0.0006939372739329904, 'alpha': 0.06422225418757876, 'max_depth': 7, 'eta': 0.03110327864818402, 'gamma': 0.002934248194107997, 'grow_policy': 'depthwise', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}. Best is trial 247 with value: 0.6703296703296703.


----------------------------
hyperparameters: {'booster': 'dart', 'lambda': 0.0444695765439596, 'alpha': 0.01786111277878498, 'max_depth': 8, 'eta': 0.033112311269453534, 'gamma': 0.029464058638134023, 'grow_policy': 'depthwise', 'sample_type': 'uniform', 'normalize_type': 'tree', 'rate_drop': 2.3191289124392886e-05, 'skip_drop': 1.1855748495043096e-07, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.608902
[1]	validation-auc:0.613963
[2]	validation-auc:0.648659
[3]	validation-auc:0.65061
[4]	validation-auc:0.646098
[5]	validation-auc:0.653659
[6]	validation-auc:0.648537
[7]	validation-auc:0.661951
[8]	validation-auc:0.661524
[9]	validation-auc:0.658476
2. test  xgboost
F1: 0.6208791208791209
F1_macro: 0.6203174603174604
Recall: 0.6208791208791209
Recall_macro: 0.6231707317073171
Precision: 0.6208791208791209
Precision_macro: 0.6220248882445331
Accuarcy:  0.6208791208791209


[I 2020-08-22 19:54:48,891] Trial 299 finished with value: 0.6208791208791209 and parameters: {'booster': 'dart', 'lambda': 0.0444695765439596, 'alpha': 0.01786111277878498, 'max_depth': 8, 'eta': 0.033112311269453534, 'gamma': 0.029464058638134023, 'grow_policy': 'depthwise', 'sample_type': 'uniform', 'normalize_type': 'tree', 'rate_drop': 2.3191289124392886e-05, 'skip_drop': 1.1855748495043096e-07, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}. Best is trial 247 with value: 0.6703296703296703.


FrozenTrial(number=247, value=0.6703296703296703, datetime_start=datetime.datetime(2020, 8, 22, 19, 54, 41, 502399), datetime_complete=datetime.datetime(2020, 8, 22, 19, 54, 41, 641100), params={'booster': 'dart', 'lambda': 0.0013280328491400604, 'alpha': 0.025152134201752347, 'max_depth': 8, 'eta': 0.028392506433058056, 'gamma': 0.0039695173148429725, 'grow_policy': 'depthwise', 'sample_type': 'uniform', 'normalize_type': 'tree', 'rate_drop': 1.3087768572894843e-05, 'skip_drop': 4.0280220181036883e-07, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}, distributions={'booster': CategoricalDistribution(choices=('gbtree', 'gblinear', 'dart')), 'lambda': LogUniformDistribution(high=1.0, low=1e-08), 'alpha': LogUniformDistribution(high=1.0, low=1e-08), 'max_depth': IntUniformDistribution(high=9, low=1, step=1), 'eta': LogUniformDistribution(high=1.0, low=1e-08), 'gamma': LogUniformDistribution(high=1.0, low=1e-08), 'grow_policy': CategoricalDistribution(choices=('depthwise', '

In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'booster': 'dart', 'lambda': 0.0013280328491400604, 'alpha': 0.025152134201752347, 'max_depth': 8, 'eta': 0.028392506433058056, 'gamma': 0.0039695173148429725, 'grow_policy': 'depthwise', 'sample_type': 'uniform', 'normalize_type': 'tree', 'rate_drop': 1.3087768572894843e-05, 'skip_drop': 4.0280220181036883e-07, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True} accuracy:0.6703296703296703


XGBoost Distance 12

In [ ]:
study = optuna.create_study(
        pruner=optuna.pruners.MedianPruner(n_warmup_steps=5), direction="maximize"
    )
study.optimize(startxgboostModelobjectiveGLCMDistance12, n_trials=300)
print(study.best_trial)
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

NameError: ignored

In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

NameError: ignored

In [ ]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns; sns.set()

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning:

pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.



In [ ]:
from sklearn.metrics import confusion_matrix
mat = confusion_matrix(ytest, ypred)
sns.heatmap(mat.T, square=True, annot=True, fmt='d', cbar=False)
plt.xlabel('true label')
plt.ylabel('predicted label');

# Train and Predict LBP

Optimization LBP

In [ ]:
def lbpObjectiveRFAll(trial):
  redios = None
  return lbpObjectiveRF(trial, redios);

In [ ]:
def lbpObjectiveRF19(trial):
  redios = 19
  return lbpObjectiveRF(trial, redios);

In [ ]:
def lbpObjectiveRF(trial, redios):
  #NbPoints = 8
  if redios == None:
    redios = trial.suggest_int('redios', 1, 20)

  print('--- LBP redios:', redios)
  train_features= LBP_f[redios]["train"]["features"]
  train_features_normalized= LBP_f[redios]["train"]["features_normalized"]
  train_labels_categorial=LBP_f[redios]['train']['categorial_labels']

  test_features= LBP_f[redios]["test"]["features"]
  test_features_normalized= LBP_f[redios]["test"]["features_normalized"]
  test_labels_categorial=LBP_f[redios]['test']['categorial_labels']

  rf_max_depth = trial.suggest_int('rf_max_depth', 2, 100)  # max_depth represents the depth of each tree in the forest
  rf_n_estimators = trial.suggest_int('n_estimators', 10, 1000)  #n_estimators represents the number of trees in the forest.
  rf_min_samples_splits  = trial.suggest_int('rf_min_samples_splits', 2, 10)
  apply_Entropy = trial.suggest_categorical("apply_Entropy", [True, False])

  model = RandomForestClassifier(n_estimators=rf_n_estimators, max_depth=rf_max_depth, min_samples_split = rf_min_samples_splits , random_state=0, criterion='entropy' if apply_Entropy else 'gini')      
  
  apply_NormalizedFeatures = trial.suggest_categorical("apply_NormalizedFeatures", [True, False])
  modelName = 'RF'
  if apply_NormalizedFeatures:  
      modelFited = trainClassifier(np.array(train_features_normalized), train_labels_categorial, model)
      acc = testModel(modelFited, np.array(test_features_normalized) ,test_labels_categorial )
  else:          
    modelFited = trainClassifier(np.array(train_features), train_labels_categorial, model)
    acc = testModel(modelFited, np.array(test_features) ,test_labels_categorial )

  return acc

In [ ]:
def lbpObjectiveKNNAll(trial):
  redios = None
  return lbpObjectiveKNN(trial, redios);

In [ ]:
def lbpObjectiveKNN11(trial):
  redios = 11
  return lbpObjectiveKNN(trial, redios);

In [ ]:
def lbpObjectiveKNN(trial, redios):
  #NbPoints = 8
  if redios == None:
    redios = trial.suggest_int('redios', 1, 20)

  print('--- LBP redios:', redios)
  train_features= LBP_f[redios]["train"]["features"]
  train_features_normalized= LBP_f[redios]["train"]["features_normalized"]
  train_labels_categorial=LBP_f[redios]['train']['categorial_labels']

  test_features= LBP_f[redios]["test"]["features"]
  test_features_normalized= LBP_f[redios]["test"]["features_normalized"]
  test_labels_categorial=LBP_f[redios]['test']['categorial_labels']

  knn_n_neighbors = trial.suggest_int('knn_n_neighbors', 2, 150)  # max_depth represents the depth of each tree in the forest
  knn_leaf_size = trial.suggest_int('knn_leaf_size', 1, 500)  #n_estimators represents the number of trees in the forest.        
  algo = trial.suggest_categorical("algo", ["auto", "ball_tree","kd_tree","brute"])
  knn_weights = trial.suggest_categorical("knn_weights", ["uniform", "distance"])
  knn_metric = trial.suggest_categorical("knn_metric", ["minkowski", "chebyshev"])
  model = KNeighborsClassifier(n_neighbors=knn_n_neighbors, algorithm=algo)   
  
  apply_NormalizedFeatures = trial.suggest_categorical("apply_NormalizedFeatures", [True, False])
  modelName = 'Knn'
  if apply_NormalizedFeatures:  
      modelFited = trainClassifier(np.array(train_features_normalized), train_labels_categorial, model)
      acc = testModel(modelFited, np.array(test_features_normalized) ,test_labels_categorial )
  else:          
    modelFited = trainClassifier(np.array(train_features), train_labels_categorial, model)
    acc = testModel(modelFited, np.array(test_features) ,test_labels_categorial )

  return acc

In [ ]:
def startxgboostLBPObjectiveAll(trial):
  redios = None
  startxgboostLBP(trial, redios)

In [ ]:
def startxgboostLBPObjective_Distance3(trial):
  redios = 3
  startxgboostLBP(trial, redios)

In [ ]:
def startxgboostLBP(trial, redios):  
        if redios == None:
          redios = trial.suggest_int('redios', 1, 20)

        train_features= LBP_f[redios]["train"]["features"]
        train_features_normalized= LBP_f[redios]["train"]["features_normalized"]
        train_labels_categorial=LBP_f[redios]['train']['categorial_labels']

        test_features= LBP_f[redios]["test"]["features"]
        test_features_normalized= LBP_f[redios]["test"]["features_normalized"]
        test_labels_categorial=LBP_f[redios]['test']['categorial_labels']
        
        param = {
        "silent": 1,
        "objective": "binary:logistic",
        "eval_metric": "auc",
        "booster": trial.suggest_categorical("booster", ["gbtree", "gblinear", "dart"]),
        "lambda": trial.suggest_float("lambda", 1e-8, 1.0, log=True),
        "alpha": trial.suggest_float("alpha", 1e-8, 1.0, log=True),
        }

        if param["booster"] == "gbtree" or param["booster"] == "dart":
            param["max_depth"] = trial.suggest_int("max_depth", 1, 9)
            param["eta"] = trial.suggest_float("eta", 1e-8, 1.0, log=True)
            param["gamma"] = trial.suggest_float("gamma", 1e-8, 1.0, log=True)
            param["grow_policy"] = trial.suggest_categorical("grow_policy", ["depthwise", "lossguide"])
        if param["booster"] == "dart":
            param["sample_type"] = trial.suggest_categorical("sample_type", ["uniform", "weighted"])
            param["normalize_type"] = trial.suggest_categorical("normalize_type", ["tree", "forest"])
            param["rate_drop"] = trial.suggest_float("rate_drop", 1e-8, 1.0, log=True)
            param["skip_drop"] = trial.suggest_float("skip_drop", 1e-8, 1.0, log=True)


        # Add a callback for pruning.
        pruning_callback = optuna.integration.XGBoostPruningCallback(trial, "validation-auc")

        apply_fullFeatures = trial.suggest_categorical("apply_fullFeatures", [True, False])
        apply_NormalizedFeatures = trial.suggest_categorical("apply_NormalizedFeatures", [True, False])

        print('----------------------------')
        print("hyperparameters: {}".format(trial.params))
        modelName = 'xgboost'

        apply_NormalizedFeatures = trial.suggest_categorical("apply_NormalizedFeatures", [True, False])        
        if apply_NormalizedFeatures:  
            dtrain = xgb.DMatrix(np.array(train_features_normalized), label=train_labels_categorial)
            dvalid = xgb.DMatrix(np.array(test_features_normalized), label=test_labels_categorial)       
            print('1. train ', modelName)
            modelFited = xgb.train(param, dtrain, evals=[(dvalid, "validation")], callbacks=[pruning_callback])
            print('2. test ',modelName)
            preds = modelFited.predict(dvalid)
            pred_labels = np.rint(preds)
            acc = accuracy_score(test_labels_categorial, pred_labels)
        else:          
            print('1. train ', modelName)
            dtrain = xgb.DMatrix(np.array(train_features), label=train_labels_categorial)
            dvalid = xgb.DMatrix(np.array(test_features), label=test_labels_categorial)   
            modelFited = xgb.train(param, dtrain, evals=[(dvalid, "validation")], callbacks=[pruning_callback])
            print('2. test ',modelName)
            preds = modelFited.predict(dvalid)
            pred_labels = np.rint(preds)
            acc = accuracy_score(test_labels_categorial, pred_labels)
               

        test_labels = test_labels_categorial
        pred_data = pred_labels
        print("F1: " + str(f1_score(test_labels, pred_data, average='micro')))
        print("F1_macro: " + str(f1_score(test_labels, pred_data, average='macro')))
        print("Recall: " + str(recall_score(test_labels, pred_data, average='micro')))
        print("Recall_macro: " + str(recall_score(test_labels, pred_data, average='macro')))
        print("Precision: " + str(precision_score(test_labels, pred_data, average='micro')))
        print("Precision_macro: " + str(precision_score(test_labels, pred_data, average='macro')))               
    #except: 
    #  acc = 0
    #return acc
        print('Accuarcy: ', acc)
        return acc

LBP XGB 

In [ ]:
study = optuna.create_study(
        pruner=optuna.pruners.MedianPruner(n_warmup_steps=5), direction="maximize"
    )
study.optimize(startxgboostLBPObjectiveAll, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

----------------------------
hyperparameters: {'redios': 3, 'booster': 'gbtree', 'lambda': 0.14137971510383743, 'alpha': 0.0017364323476781838, 'max_depth': 7, 'eta': 3.044975559198873e-06, 'gamma': 4.965158187768292e-08, 'grow_policy': 'lossguide', 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.537561
[1]	validation-auc:0.537317
[2]	validation-auc:0.537317
[3]	validation-auc:0.537317
[4]	validation-auc:0.537317
[5]	validation-auc:0.537317
[6]	validation-auc:0.537317
[7]	validation-auc:0.537317
[8]	validation-auc:0.537317
[9]	validation-auc:0.537317
2. test  xgboost
F1: 0.5494505494505495
F1_macro: 0.5414772029003319
Recall: 0.5494505494505495
Recall_macro: 0.5417073170731708
Precision: 0.5494505494505495
Precision_macro: 0.5424528301886793
Accuarcy:  0.5494505494505495


[W 2020-08-23 06:56:05,540] Trial 0 failed, because the returned value from the objective function cannot be cast to float. Returned value is: None


----------------------------
hyperparameters: {'redios': 5, 'booster': 'gblinear', 'lambda': 3.869204155558783e-08, 'alpha': 1.0625165468059765e-06, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.588659
[1]	validation-auc:0.588659
[2]	validation-auc:0.588659
[3]	validation-auc:0.588659
[4]	validation-auc:0.588659
[5]	validation-auc:0.588659
[6]	validation-auc:0.588659
[7]	validation-auc:0.588659
[8]	validation-auc:0.588659
[9]	validation-auc:0.588659
2. test  xgboost
F1: 0.5604395604395604
F1_macro: 0.39099882884390164
Recall: 0.5604395604395604
Recall_macro: 0.5132926829268293
Precision: 0.5604395604395604
Precision_macro: 0.6530898876404494
Accuarcy:  0.5604395604395604


[W 2020-08-23 06:56:05,611] Trial 1 failed, because the returned value from the objective function cannot be cast to float. Returned value is: None


----------------------------
hyperparameters: {'redios': 2, 'booster': 'gblinear', 'lambda': 0.265831579256632, 'alpha': 0.0027439094160204387, 'apply_fullFeatures': False, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.525549
[1]	validation-auc:0.525366
[2]	validation-auc:0.525122
[3]	validation-auc:0.525183
[4]	validation-auc:0.524939
[5]	validation-auc:0.525122
[6]	validation-auc:0.525061
[7]	validation-auc:0.525122
[8]	validation-auc:0.525244
[9]	validation-auc:0.525183
2. test  xgboost
F1: 0.5494505494505495
F1_macro: 0.3546099290780142
Recall: 0.5494505494505495
Recall_macro: 0.5
Precision: 0.5494505494505495


...

----------------------------
hyperparameters: {'redios': 5, 'booster': 'gblinear', 'lambda': 1.680490581891614e-08, 'alpha': 6.685287462100251e-05, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.588659
[1]	validation-auc:0.588659
[2]	validation-auc:0.588659
[3]	validation-auc:0.588659
[4]	validation-auc:0.588659
[5]	validation-auc:0.588659
[6]	validation-auc:0.588659
[7]	validation-auc:0.588659
[8]	validation-auc:0.588659
[9]	validation-auc:0.588659
2. test  xgboost
F1: 0.5659340659340659
F1_macro: 0.3937170567151591
Recall: 0.5659340659340659
Recall_macro: 0.5182926829268293
Precision: 0.5659340659340659
Precision_macro: 0.7793296089385475
Accuarcy:  0.5659340659340659


[W 2020-08-23 06:56:32,907] Trial 298 failed, because the returned value from the objective function cannot be cast to float. Returned value is: None


----------------------------
hyperparameters: {'redios': 5, 'booster': 'dart', 'lambda': 1.9135996237291225e-07, 'alpha': 0.00024280509868182846, 'max_depth': 1, 'eta': 0.004387391994380094, 'gamma': 0.00010906019850703511, 'grow_policy': 'lossguide', 'sample_type': 'weighted', 'normalize_type': 'forest', 'rate_drop': 0.008621726991429091, 'skip_drop': 0.4350000440511733, 'apply_fullFeatures': True, 'apply_NormalizedFeatures': True}
1. train  xgboost
[0]	validation-auc:0.571463
[1]	validation-auc:0.571463
[2]	validation-auc:0.571463
[3]	validation-auc:0.571463
[4]	validation-auc:0.571463
[5]	validation-auc:0.571463
[6]	validation-auc:0.571463
[7]	validation-auc:0.571463
[8]	validation-auc:0.571463
[9]	validation-auc:0.571463
2. test  xgboost
F1: 0.5604395604395604
F1_macro: 0.5591085271317829
Recall: 0.5604395604395604
Recall_macro: 0.5714634146341464
Precision: 0.5604395604395604
Precision_macro: 0.5739898989898989
Accuarcy:  0.5604395604395604


[W 2020-08-23 06:56:33,008] Trial 299 failed, because the returned value from the objective function cannot be cast to float. Returned value is: None


ValueError: ignored

In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

NameError: ignored

LBP RF

In [ ]:
study = optuna.create_study(direction='maximize')  # Create a new study.
study.optimize(lbpObjectiveRFAll, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

--- LBP redios: 19
F1: 0.5054945054945055
F1_macro: 0.5033353547604609
Recall: 0.5054945054945055
Recall_macro: 0.5178571428571428
Precision: 0.5054945054945055
Precision_macro: 0.5170731707317073
Accuracy:0.5054945054945055
-----------------------------------------


[I 2020-08-22 20:33:26,075] Trial 0 finished with value: 0.5054945054945055 and parameters: {'redios': 19, 'rf_max_depth': 67, 'n_estimators': 622, 'rf_min_samples_splits': 6, 'apply_Entropy': False, 'apply_NormalizedFeatures': True}. Best is trial 0 with value: 0.5054945054945055.


--- LBP redios: 12
F1: 0.5274725274725275
F1_macro: 0.5265577737447066
Recall: 0.5274725274725275
Recall_macro: 0.5280193236714976
Precision: 0.5274725274725275
Precision_macro: 0.5282926829268293
Accuracy:0.5274725274725275
-----------------------------------------


[I 2020-08-22 20:33:27,766] Trial 1 finished with value: 0.5274725274725275 and parameters: {'redios': 12, 'rf_max_depth': 95, 'n_estimators': 920, 'rf_min_samples_splits': 2, 'apply_Entropy': True, 'apply_NormalizedFeatures': False}. Best is trial 1 with value: 0.5274725274725275.


--- LBP redios: 18
F1: 0.4945054945054945
F1_macro: 0.4870098039215687
Recall: 0.4945054945054945
Recall_macro: 0.5128415300546448
Precision: 0.4945054945054945
Precision_macro: 0.5114634146341464
Accuracy:0.4945054945054945
-----------------------------------------


...

--- LBP redios: 18
F1: 0.6098901098901099
F1_macro: 0.6097840857617394
Recall: 0.6098901098901099
Recall_macro: 0.6184711810249477
Precision: 0.6098901098901099
Precision_macro: 0.6175609756097561
Accuracy:0.6098901098901099
-----------------------------------------


[I 2020-08-22 20:35:15,939] Trial 298 finished with value: 0.6098901098901099 and parameters: {'redios': 18, 'rf_max_depth': 29, 'n_estimators': 131, 'rf_min_samples_splits': 10, 'apply_Entropy': True, 'apply_NormalizedFeatures': False}. Best is trial 129 with value: 0.6208791208791209.


--- LBP redios: 19
F1: 0.5934065934065934
F1_macro: 0.5862111343246896
Recall: 0.5934065934065934
Recall_macro: 0.6281979977753058
Precision: 0.5934065934065934
Precision_macro: 0.6124390243902439
Accuracy:0.5934065934065934
-----------------------------------------


[I 2020-08-22 20:35:16,166] Trial 299 finished with value: 0.5934065934065934 and parameters: {'redios': 19, 'rf_max_depth': 44, 'n_estimators': 83, 'rf_min_samples_splits': 10, 'apply_Entropy': True, 'apply_NormalizedFeatures': False}. Best is trial 129 with value: 0.6208791208791209.


Best hyperparameters: {'redios': 19, 'rf_max_depth': 78, 'n_estimators': 95, 'rf_min_samples_splits': 10, 'apply_Entropy': True, 'apply_NormalizedFeatures': False} accuracy:0.6208791208791209


In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'redios': 19, 'rf_max_depth': 78, 'n_estimators': 95, 'rf_min_samples_splits': 10, 'apply_Entropy': True, 'apply_NormalizedFeatures': False} accuracy:0.6208791208791209


LBP RF radios 19

In [ ]:
study = optuna.create_study(direction='maximize')  # Create a new study.
study.optimize(lbpObjectiveRF19, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

--- LBP redios: 19
F1: 0.5989010989010989
F1_macro: 0.5934889698008139
Recall: 0.5989010989010989
Recall_macro: 0.6292507790272321
Precision: 0.5989010989010989
Precision_macro: 0.6163414634146341
Accuracy:0.5989010989010989
-----------------------------------------


[I 2020-08-22 20:41:02,746] Trial 0 finished with value: 0.5989010989010989 and parameters: {'rf_max_depth': 34, 'n_estimators': 272, 'rf_min_samples_splits': 9, 'apply_Entropy': False, 'apply_NormalizedFeatures': False}. Best is trial 0 with value: 0.5989010989010989.


--- LBP redios: 19
F1: 0.554945054945055
F1_macro: 0.5433509896849735
Recall: 0.554945054945055
Recall_macro: 0.5915606260055579
Precision: 0.554945054945055
Precision_macro: 0.5763414634146342
Accuracy:0.554945054945055
-----------------------------------------


[I 2020-08-22 20:41:04,078] Trial 1 finished with value: 0.554945054945055 and parameters: {'rf_max_depth': 7, 'n_estimators': 733, 'rf_min_samples_splits': 4, 'apply_Entropy': True, 'apply_NormalizedFeatures': False}. Best is trial 0 with value: 0.5989010989010989.


--- LBP redios: 19
F1: 0.5659340659340659
F1_macro: 0.5611512987211182
Recall: 0.5659340659340659
Recall_macro: 0.5896358543417366
Precision: 0.5659340659340659
Precision_macro: 0.5819512195121951
Accuracy:0.5659340659340659
-----------------------------------------


...

--- LBP redios: 19
F1: 0.6153846153846154
F1_macro: 0.6115853658536585
Recall: 0.6153846153846154
Recall_macro: 0.6426112288135593
Precision: 0.6153846153846154
Precision_macro: 0.6313414634146342
Accuracy:0.6153846153846154
-----------------------------------------


[I 2020-08-22 20:42:47,649] Trial 298 finished with value: 0.6153846153846154 and parameters: {'rf_max_depth': 29, 'n_estimators': 101, 'rf_min_samples_splits': 10, 'apply_Entropy': False, 'apply_NormalizedFeatures': False}. Best is trial 62 with value: 0.6208791208791209.


--- LBP redios: 19
F1: 0.6153846153846154
F1_macro: 0.6115853658536585
Recall: 0.6153846153846154
Recall_macro: 0.6426112288135593
Precision: 0.6153846153846154
Precision_macro: 0.6313414634146342
Accuracy:0.6153846153846154
-----------------------------------------


[I 2020-08-22 20:42:47,974] Trial 299 finished with value: 0.6153846153846154 and parameters: {'rf_max_depth': 63, 'n_estimators': 164, 'rf_min_samples_splits': 10, 'apply_Entropy': False, 'apply_NormalizedFeatures': False}. Best is trial 62 with value: 0.6208791208791209.


Best hyperparameters: {'rf_max_depth': 37, 'n_estimators': 125, 'rf_min_samples_splits': 10, 'apply_Entropy': False, 'apply_NormalizedFeatures': False} accuracy:0.6208791208791209


In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'rf_max_depth': 37, 'n_estimators': 125, 'rf_min_samples_splits': 10, 'apply_Entropy': False, 'apply_NormalizedFeatures': False} accuracy:0.6208791208791209


LBP KNN

In [ ]:
study = optuna.create_study(direction='maximize')  # Create a new study.
study.optimize(lbpObjectiveKNNAll, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

--- LBP redios: 7
F1: 0.5274725274725275
F1_macro: 0.5274725274725274
Recall: 0.5274725274725275
Recall_macro: 0.5326829268292683
Precision: 0.5274725274725275
Precision_macro: 0.5326829268292683
Accuracy:0.5274725274725275
-----------------------------------------


[I 2020-08-22 20:48:44,304] Trial 0 finished with value: 0.5274725274725275 and parameters: {'redios': 7, 'knn_n_neighbors': 14, 'knn_leaf_size': 274, 'algo': 'ball_tree', 'knn_weights': 'distance', 'knn_metric': 'minkowski', 'apply_NormalizedFeatures': False}. Best is trial 0 with value: 0.5274725274725275.


--- LBP redios: 18
F1: 0.554945054945055
F1_macro: 0.5526627218934912
Recall: 0.554945054945055
Recall_macro: 0.5710529690906758
Precision: 0.554945054945055
Precision_macro: 0.567560975609756
Accuracy:0.554945054945055
-----------------------------------------


[I 2020-08-22 20:48:44,365] Trial 1 finished with value: 0.554945054945055 and parameters: {'redios': 18, 'knn_n_neighbors': 25, 'knn_leaf_size': 134, 'algo': 'brute', 'knn_weights': 'uniform', 'knn_metric': 'chebyshev', 'apply_NormalizedFeatures': False}. Best is trial 1 with value: 0.554945054945055.


--- LBP redios: 9
F1: 0.5604395604395604
F1_macro: 0.5550666177728885
Recall: 0.5604395604395604
Recall_macro: 0.5848118279569892
Precision: 0.5604395604395604
Precision_macro: 0.5769512195121951
Accuracy:0.5604395604395604
-----------------------------------------


...

--- LBP redios: 12
F1: 0.510989010989011
F1_macro: 0.5106196561829662
Recall: 0.510989010989011
Recall_macro: 0.519047619047619
Precision: 0.510989010989011
Precision_macro: 0.5187804878048781
Accuracy:0.510989010989011
-----------------------------------------


[I 2020-08-22 20:49:06,123] Trial 298 finished with value: 0.510989010989011 and parameters: {'redios': 12, 'knn_n_neighbors': 21, 'knn_leaf_size': 436, 'algo': 'kd_tree', 'knn_weights': 'distance', 'knn_metric': 'chebyshev', 'apply_NormalizedFeatures': False}. Best is trial 48 with value: 0.6373626373626373.


--- LBP redios: 11
F1: 0.5824175824175825
F1_macro: 0.5799319727891156
Recall: 0.5824175824175825
Recall_macro: 0.5799418604651163
Precision: 0.5824175824175825
Precision_macro: 0.5804878048780489
Accuracy:0.5824175824175825
-----------------------------------------


[I 2020-08-22 20:49:06,206] Trial 299 finished with value: 0.5824175824175825 and parameters: {'redios': 11, 'knn_n_neighbors': 18, 'knn_leaf_size': 459, 'algo': 'kd_tree', 'knn_weights': 'distance', 'knn_metric': 'chebyshev', 'apply_NormalizedFeatures': False}. Best is trial 48 with value: 0.6373626373626373.


Best hyperparameters: {'redios': 11, 'knn_n_neighbors': 21, 'knn_leaf_size': 366, 'algo': 'kd_tree', 'knn_weights': 'distance', 'knn_metric': 'chebyshev', 'apply_NormalizedFeatures': False} accuracy:0.6373626373626373


In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'redios': 11, 'knn_n_neighbors': 21, 'knn_leaf_size': 366, 'algo': 'kd_tree', 'knn_weights': 'distance', 'knn_metric': 'chebyshev', 'apply_NormalizedFeatures': False} accuracy:0.6373626373626373


LBP KNN redios 11

In [ ]:
study = optuna.create_study(direction='maximize')  # Create a new study.
study.optimize(lbpObjectiveKNN11, n_trials=300)  # Invoke optimization of the objective function.
trial = study.best_trial
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

--- LBP redios: 11
F1: 0.521978021978022
F1_macro: 0.45690276110444183
Recall: 0.521978021978022
Recall_macro: 0.4886300093196645
Precision: 0.521978021978022
Precision_macro: 0.4925609756097561
Accuracy:0.521978021978022
-----------------------------------------


[I 2020-08-22 20:51:43,817] Trial 0 finished with value: 0.521978021978022 and parameters: {'knn_n_neighbors': 2, 'knn_leaf_size': 427, 'algo': 'brute', 'knn_weights': 'distance', 'knn_metric': 'chebyshev', 'apply_NormalizedFeatures': True}. Best is trial 0 with value: 0.521978021978022.


--- LBP redios: 11
F1: 0.510989010989011
F1_macro: 0.4943655376931481
Recall: 0.510989010989011
Recall_macro: 0.5429645542427497
Precision: 0.510989010989011
Precision_macro: 0.5341463414634147
Accuracy:0.510989010989011
-----------------------------------------


[I 2020-08-22 20:51:43,878] Trial 1 finished with value: 0.510989010989011 and parameters: {'knn_n_neighbors': 103, 'knn_leaf_size': 154, 'algo': 'kd_tree', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_NormalizedFeatures': True}. Best is trial 0 with value: 0.521978021978022.


--- LBP redios: 11
F1: 0.5274725274725275
F1_macro: 0.5176282051282052
Recall: 0.5274725274725275
Recall_macro: 0.5545634920634921
Precision: 0.5274725274725275
Precision_macro: 0.546951219512195
Accuracy:0.5274725274725275
-----------------------------------------


...

--- LBP redios: 11
F1: 0.5384615384615384
F1_macro: 0.5384057971014492
Recall: 0.5384615384615384
Recall_macro: 0.5450980392156862
Precision: 0.5384615384615384
Precision_macro: 0.5448780487804878
Accuracy:0.5384615384615384
-----------------------------------------


[I 2020-08-22 20:52:05,192] Trial 298 finished with value: 0.5384615384615384 and parameters: {'knn_n_neighbors': 15, 'knn_leaf_size': 349, 'algo': 'auto', 'knn_weights': 'uniform', 'knn_metric': 'minkowski', 'apply_NormalizedFeatures': False}. Best is trial 17 with value: 0.6373626373626373.


--- LBP redios: 11
F1: 0.5824175824175825
F1_macro: 0.5799319727891156
Recall: 0.5824175824175825
Recall_macro: 0.5799418604651163
Precision: 0.5824175824175825
Precision_macro: 0.5804878048780489
Accuracy:0.5824175824175825
-----------------------------------------


[I 2020-08-22 20:52:05,265] Trial 299 finished with value: 0.5824175824175825 and parameters: {'knn_n_neighbors': 18, 'knn_leaf_size': 24, 'algo': 'auto', 'knn_weights': 'distance', 'knn_metric': 'minkowski', 'apply_NormalizedFeatures': False}. Best is trial 17 with value: 0.6373626373626373.


Best hyperparameters: {'knn_n_neighbors': 21, 'knn_leaf_size': 150, 'algo': 'brute', 'knn_weights': 'distance', 'knn_metric': 'minkowski', 'apply_NormalizedFeatures': False} accuracy:0.6373626373626373


In [ ]:
print("Best hyperparameters: {} accuracy:{}".format(trial.params, study.best_value))

Best hyperparameters: {'knn_n_neighbors': 21, 'knn_leaf_size': 150, 'algo': 'brute', 'knn_weights': 'distance', 'knn_metric': 'minkowski', 'apply_NormalizedFeatures': False} accuracy:0.6373626373626373
